# Statement
With the keyword "Istanbul", I scraped 110 books from OpenLibrary. Then I extracted txt files according to the input 28 keywords about objects in Istanbul(balcony, bench, bicycle parking, bus stop, carpet, cash machine, cat, cat food, cat house, chair, dilapidated building,entrance, garbage, garbage can, hanging clothes, kiosk, lamp post, mosaic tiles, parasol, staircase, table, tea kiosk, tram, tram station, umbrella, vending cart, vendor, water tap).  

datatype of the dataset: text format txt

In [29]:
from selenium import webdriver
from selenium.webdriver.common.by import By
import time

import json
import csv
import urllib.request

from selenium.webdriver.firefox.options import Options

In [30]:
csv_filename = 'istanbul_books9.csv'

In [31]:
#Create empyt csv file with dictionary headers before running the scraping 
#(Make sure not to run this with the same filename as it will erase the old file)

with open(csv_filename, 'w', newline='') as csvfile:
    fieldnames = ['title','subtitle','date','txt','gif','pdf','openURL', 'index']
    writer = csv.DictWriter(csvfile, fieldnames = fieldnames)
    writer.writeheader()
    csvfile.close()

In [32]:
from selenium.webdriver.firefox.options import Options
from selenium.webdriver.firefox.firefox_binary import FirefoxBinary
from selenium import webdriver

options = Options()
options.headless = False

firefox_binary_path = 'C:/Program Files/Mozilla Firefox/firefox.exe'  # Update with the correct path to your Firefox binary

firefox_binary = FirefoxBinary(firefox_binary_path)


In [33]:
driver = webdriver.Firefox(firefox_binary=firefox_binary, executable_path='C:/Users/user/Downloads/code/geckodriver', options=options)
driver.get('https://archive.org/details/texts?query=istanbul&and[]=mediatype%3A%22texts%22&and[]=lending___status%3A%22is_readable%22&and[]=languageSorter%3A%22English%22')

In [34]:
for i in range(20):
    print(i)
    
    books = driver.find_elements(By.CLASS_NAME, 'item-ttl.C.C2')
    book_links = [b.find_element(By.TAG_NAME, 'a').get_attribute('href') for b in books][-75:]


    for b in book_links:
        driver.get(b)

        try:
            downloads = driver.find_element(By.PARTIAL_LINK_TEXT, 'SHOW ALL')
            downloads.click()
        except:
            downloads = False

        if downloads:
            try:
                txt = driver.find_element(By.PARTIAL_LINK_TEXT, '.txt').get_attribute('href')
            except:
                txt = None
            try:
                gif = driver.find_element(By.PARTIAL_LINK_TEXT, '.gif').get_attribute('href')
            except:
                gif = None
            try:
                pdf = driver.find_element(By.PARTIAL_LINK_TEXT, '.pdf').get_attribute('href')
            except:
                pdf = None

        driver.back()

        try:
            title = driver.find_element(By.XPATH, "/html/body/div[1]/main/div[4]/div/div/div[2]/h1/span").text
        except:
            title = None
        try:
            subtitle = driver.find_element(By.XPATH, "/html/body/div[1]/main/div[4]/div/div/div[2]/dl/dd/span/a").text
        except:
            subtitle = None
        try:
            date = driver.find_element(By.XPATH, "/html/body/div[1]/main/div[5]/div/div/div[1]/div[2]/dl[1]/dd").text
        except:
            date = None

        iName = b.split('/')[-1]
        index = 'OL'+iName+'.txt'

        book = {'title':title,
                'subtitle': subtitle,
                'date': date,
                'txt': txt,
                'gif': gif,
                'pdf': pdf,
                'openURL':b,
                'index': index
               }

        with open(csv_filename, 'a', newline = '', encoding='utf-8') as csvfile:
            writer = csv.DictWriter(csvfile, fieldnames = fieldnames)
            writer.writerow(book)

        driver.back()
    
    driver.execute_script("window.scrollTo(0,document.body.scrollHeight)")
    time.sleep(3)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19


In [35]:
import pprint
import nltk.corpus
import random
import os
import gensim

In [36]:
nltk.download('words')

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\user\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


True

In [37]:
read_books = []
csv_filename = 'istanbul_books9.csv'
with open(csv_filename, newline='') as csvfile:
    reader = csv.DictReader(csvfile)
    for row in reader:
        read_books.append(row)

In [46]:
len(read_books)

780

In [47]:
read_books[1]

{'title': "Advances in multimedia information systems : 4th international workshop, MIS'98, Istanbul, Turkey, September 24-26, 1998 : proceedings",
 'subtitle': 'Jajodia, Sushil',
 'date': '1998',
 'txt': 'https://archive.org/download/springer_10.1007-3-540-49651-3/10.1007-3-540-49651-3_djvu.txt',
 'gif': 'https://archive.org/download/springer_10.1007-3-540-49651-3/10.1007-3-540-49651-3.gif',
 'pdf': 'https://archive.org/download/springer_10.1007-3-540-49651-3/10.1007-3-540-49651-3.pdf',
 'openURL': 'https://archive.org/details/springer_10.1007-3-540-49651-3',
 'index': 'OLspringer_10.1007-3-540-49651-3.txt'}

In [51]:
def save_text(book, directory):
    text = ""
    for line in urllib.request.urlopen(book['txt']):
        text += str(line)
    f = open(os.path.join(directory, book['index']),"w")
    f.write(text)
    f.close()
    

In [53]:
def isEnglish(book, word_dictionary):
    filename = os.path.join('books', book['index'])
    
    f = open(filename,'r')
    text = f.read()
    
    words = text.split(' ')
    random.shuffle(words)
    
    english_found = False
    for w in words[:1000]:
        if w in word_dictionary:
            return True
    return False

In [55]:
for b in read_books:
    b = save_text(b, 'books')

In [456]:
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize
import os

combined_sentences = []
sentence_book_index = []

read_english_books = []
word_dictionary = nltk.corpus.words.words()

for b in read_books:
    if isEnglish(b, word_dictionary):
        read_english_books.append(b)

for b in read_books:
    filename = os.path.join('books', b['index'])
    f = open(filename, "r")
    text = f.read()
    paragraphs = text.split("b'\\n'")
    paragraphs2 = [x.replace("b'","").replace('b"', "").replace("\\n'","").replace('\\n"',"") for x in paragraphs]
    paragraphs3 = [x.replace("\\", "").replace('^', "") for x in paragraphs2]
    paragraphs4 = [x for x in paragraphs3 if len(x)>100]

    for p in paragraphs4:
        sentences = sent_tokenize(p)
        for s in sentences:
            combined_sentences.append(s)
            sentence_book_index.append(b['index'])

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\user\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [457]:
len(combined_sentences)

3662154

In [458]:
combined_sentences[0]

'xe2x80x9cOnly three people in the world will know your real purpose,xe2x80x9d said the man in the mask.'

In [459]:
stoplist = set('for a of the and to in'.split(' '))

# In the lecture I made an error here by combining these two lines, which added words 
#in a different form in a way they shouldn't

texts = [[word.replace(".","").replace(",","") for word in document.lower().split()] 
         for document in combined_sentences]

texts = [[word for word in text if (word not in stoplist and len(word)>2)] 
         for text in texts]

to_delete = []
for i in range(len(texts)):
    t = texts[i]
    test = [w for w in t if w.isalpha()]
    if len(test) < 20:
        to_delete.append(i)
    else:
        texts[i] = test

for i in sorted(to_delete, reverse = True):
    del texts[i]
    del combined_sentences[i]
    del sentence_book_index[i]
    
# Count word frequencies
from collections import defaultdict
frequency = defaultdict(int)
for text in texts:
    for token in text:
        frequency[token] += 1

# Only keep words that appear more than once
processed_corpus = [[token for token in text if frequency[token] > 1] for text in texts]
pprint.pprint(processed_corpus[0])
        

['book',
 'sold',
 'condition',
 'that',
 'shall',
 'not',
 'tray',
 'trade',
 'lent',
 'hired',
 'out',
 'otherwise',
 'disposed',
 'consent',
 'any',
 'form',
 'binding',
 'cover',
 'other',
 'than',
 'that']


In [460]:
len(combined_sentences)

784314

In [461]:
combined_sentences[0]

'Hjis book is sold snbiect to the condition that it shall not, by tray of trade, be lent, re-BOId, hired out or otherwise disposed of .withottt the publisherxe2x80x99s consent, in any form ot binding or cover other than that in.'

In [462]:
from gensim import corpora

dictionary = corpora.Dictionary(processed_corpus)
print(dictionary)

Dictionary(97167 unique tokens: ['any', 'binding', 'book', 'condition', 'consent']...)


In [473]:
pprint.pprint(dictionary.token2id)

{'aaa': 34588,
 'aack': 37081,
 'aacred': 37965,
 'aacrificc': 35621,
 'aad': 33777,
 'aaell': 76523,
 'aaer': 36272,
 'aaerentur': 67042,
 'aaiatic': 74687,
 'aaibd': 96262,
 'aaibeys': 42268,
 'aain': 75556,
 'aainst': 82641,
 'aaioiatiod': 34656,
 'aak': 53493,
 'aali': 25960,
 'aaljlipatii': 72939,
 'aalure': 37010,
 'aame': 5605,
 'aan': 59206,
 'aanctoary': 38805,
 'aane': 33422,
 'aare': 37176,
 'aarif': 77387,
 'aaron': 43327,
 'aashik': 80652,
 'aasociated': 75295,
 'aat': 33949,
 'aatboiity': 35033,
 'aationality': 74316,
 'aatk': 41786,
 'aatonisbmeut': 36314,
 'aavcfal': 36909,
 'aavoured': 37338,
 'aawell': 73818,
 'aaxioob': 35272,
 'aay': 53280,
 'aaylum': 74387,
 'abacis': 93495,
 'aback': 42306,
 'abacus': 39187,
 'abafed': 93884,
 'abai': 73795,
 'abailard': 90037,
 'abali': 9277,
 'aban': 60752,
 'abandon': 9321,
 'abandoned': 7432,
 'abandonet': 56406,
 'abandoning': 20256,
 'abandonment': 20727,
 'abandonmg': 54553,
 'abandonnant': 78526,
 'abandonne': 78094,
 'aba

In [474]:
bow_corpus = [dictionary.doc2bow(text) for text in processed_corpus]

In [475]:
from gensim import models

tfidf = models.TfidfModel(bow_corpus)

In [476]:
from gensim.similarities import Similarity
from gensim.test.utils import get_tmpfile

In [477]:
index_tmpfile = get_tmpfile("index")

index = Similarity(index_tmpfile, bow_corpus, num_features = len(dictionary))

In [478]:
query_document = "Cash machine".lower().split()
query_bow = dictionary.doc2bow(query_document)

In [479]:
sims = index[query_bow]

In [480]:
for document_number, score in sorted(enumerate(sims), key=lambda x: x[1], reverse=True)[:250]:
    print(document_number, score)

12301 0.15811388
13940 0.15811388
25416 0.15811388
52978 0.15811388
95828 0.15811388
148637 0.15811388
183942 0.15811388
219247 0.15811388
254552 0.15811388
289857 0.15811388
325162 0.15811388
360467 0.15811388
395772 0.15811388
431077 0.15811388
466382 0.15811388
501687 0.15811388
536992 0.15811388
572297 0.15811388
607602 0.15811388
642907 0.15811388
678212 0.15811388
713517 0.15811388
748822 0.15811388
784127 0.15811388
33092 0.15430336
33094 0.15430336
75942 0.15430336
75944 0.15430336
119304 0.15430336
154609 0.15430336
189914 0.15430336
225219 0.15430336
260524 0.15430336
295829 0.15430336
331134 0.15430336
366439 0.15430336
401744 0.15430336
437049 0.15430336
472354 0.15430336
507659 0.15430336
542964 0.15430336
578269 0.15430336
613574 0.15430336
648879 0.15430336
684184 0.15430336
719489 0.15430336
754794 0.15430336
654 0.15075567
977 0.15075567
120186 0.15075567
145450 0.15075567
148622 0.15075567
155491 0.15075567
180755 0.15075567
183927 0.15075567
190796 0.15075567
216060 

In [481]:
# sort the scores in descending order and get the top 10 scores
top_scores = sorted(enumerate(sims), key=lambda x: x[1], reverse=True)[:250]

In [482]:
# create a list of the top 10 paragraphs
top_paragraphs = [combined_paragraphs[idx] for idx, score in top_scores]

# create a list of the corresponding books for the top 10 paragraphs
top_books = [paragraph_book_index[idx] for idx, score in top_scores]

# combine the top paragraphs and their corresponding books into a single string
output = ""
for i in range(len(top_paragraphs)):
    output += f"Book {top_books[i]} - Paragraph {i+1}: {top_paragraphs[i]}\n"

# write the output to a file named "top_paragraphs.txt"
with open("Cash machine.txt", "w") as f:
    f.write(output)

# print the output to the console
print(output)

Book OLconstantinoplesc01allo.txt - Paragraph 1: Flavius Basilius I., (Cephalos,) was born in Macedonia, crowned in 866, and died in 886. He was called Cephalos from the size of his head. He was a zealous promoter of image worship. In his reign, Alfred king of England died. 
Book OLstoryofjewadroma00aliarich.txt - Paragraph 2: So let the wonder-working Jewad remain viewing the power of God, wandering through towns and cities. 
Book OLprinceindiaorwh03wallgoog.txt - Paragraph 3: The  relations  of  the  Christian  and  Moslem  poten- tates being  thus  friendly,  it  can  be  seen  how  the Princess  Irene  could  keep  to  her  palace  by  Therapia and  the  Prince  of  India  plan  jaunts  along  the  Bos- phorus. 
Book OLbluegreenorgifto02pott.txt - Paragraph 4: Nor was Andreas excluded from the general satisfaction. His wet pockets were full of money, and he had the promise of Paris, who was much gratified by finding the boy sobbing sympathetically in a corner of the women's corrido

In [56]:
combined_paragraphs = []
paragraph_book_index = []

read_english_books = []
word_dictionary = nltk.corpus.words.words()
for b in read_books:
    if isEnglish(b, word_dictionary):
        read_english_books.append(b)
for b in read_books:
    filename = os.path.join('books',b['index'])
    f = open(filename, "r")
    text = f.read()
    paragraphs = text.split("b'\\n'")
    paragraphs2 = [x.replace("b'","").replace('b"', "").replace("\\n'","").replace('\\n"',"") for x in paragraphs]
    paragraphs3 = [x.replace("\\", "").replace('^', "") for x in paragraphs2]
    paragraphs4 = [x for x in paragraphs3 if len(x)>100]
    
    for p in paragraphs4:
        combined_paragraphs.append(p)
        paragraph_book_index.append(b['index'])

In [57]:
len(combined_paragraphs)

856819

In [58]:
combined_paragraphs[0]

'xe2x80x9cOnly three people in the world will know your real purpose,xe2x80x9d said the man in the mask. xe2x80x9cYou will have all the resources of this country behind you, as Y/ell as those of your own service.xe2x80x9d '

In [37]:
stoplist = set('for a of the and to in'.split(' '))

# In the lecture I made an error here by combining these two lines, which added words 
#in a different form in a way they shouldn't

texts = [[word.replace(".","").replace(",","") for word in document.lower().split()] 
         for document in combined_paragraphs]

texts = [[word for word in text if (word not in stoplist and len(word)>2)] 
         for text in texts]

to_delete = []
for i in range(len(texts)):
    t = texts[i]
    test = [w for w in t if w.isalpha()]
    if len(test) < 20:
        to_delete.append(i)
    else:
        texts[i] = test

for i in sorted(to_delete, reverse = True):
    del texts[i]
    del combined_paragraphs[i]
    del paragraph_book_index[i]
    
# Count word frequencies
from collections import defaultdict
frequency = defaultdict(int)
for text in texts:
    for token in text:
        frequency[token] += 1

# Only keep words that appear more than once
processed_corpus = [[token for token in text if frequency[token] > 1] for text in texts]
pprint.pprint(processed_corpus[0])
        

['three',
 'people',
 'world',
 'will',
 'know',
 'your',
 'real',
 'said',
 'man',
 'mask',
 'will',
 'have',
 'all',
 'resources',
 'this',
 'country',
 'behind',
 'you',
 'those',
 'your',
 'own']


In [38]:
len(combined_paragraphs)

29264

In [39]:
combined_paragraphs[0]

'xe2x80x9cOnly three people in the world will know your real purpose,xe2x80x9d said the man in the mask. xe2x80x9cYou will have all the resources of this country behind you, as Y/ell as those of your own service.xe2x80x9d '

In [40]:
from gensim import corpora

dictionary = corpora.Dictionary(processed_corpus)
print(dictionary)

Dictionary(41257 unique tokens: ['all', 'behind', 'country', 'have', 'know']...)


In [41]:
pprint.pprint(dictionary.token2id)

{'aad': 2429,
 'aadlmen': 11083,
 'aadti': 12984,
 'aaer': 40387,
 'aaid': 39882,
 'aakedaimonioi': 23736,
 'aali': 33208,
 'aalood': 10750,
 'aaloon': 10751,
 'aame': 13477,
 'aat': 39762,
 'abacus': 29095,
 'abad': 21102,
 'abali': 21350,
 'abandon': 14904,
 'abandoned': 8280,
 'abandoning': 14637,
 'abandonment': 22059,
 'abandons': 35307,
 'abasement': 35082,
 'abashed': 25892,
 'abasside': 25340,
 'abasso': 18266,
 'abate': 29392,
 'abated': 21614,
 'abatement': 28896,
 'abbas': 14290,
 'abbat': 28435,
 'abbess': 21795,
 'abbey': 24535,
 'abbot': 18206,
 'abbots': 24021,
 'abbott': 35979,
 'abbreviated': 35399,
 'abbreviation': 32243,
 'abd': 26212,
 'abdallah': 37628,
 'abderrahman': 37629,
 'abdicate': 27453,
 'abdicated': 20199,
 'abdicating': 19609,
 'abdication': 16595,
 'abdiil': 14358,
 'abdiilaziz': 11971,
 'abdiilhainit': 8910,
 'abdiilhamit': 7486,
 'abdiilhaniit': 10849,
 'abdiilmecit': 8875,
 'abdomen': 26623,
 'abdoul': 38043,
 'abdtilhamit': 9065,
 'abduct': 39349,
 

In [42]:
bow_corpus = [dictionary.doc2bow(text) for text in processed_corpus]

In [43]:
from gensim import models

tfidf = models.TfidfModel(bow_corpus)

In [44]:
from gensim.similarities import Similarity
from gensim.test.utils import get_tmpfile

In [45]:
index_tmpfile = get_tmpfile("index")

index = Similarity(index_tmpfile, bow_corpus, num_features = len(dictionary))

In [477]:
query_document = "chair".lower().split()
query_bow = dictionary.doc2bow(query_document)

In [478]:
sims = index[query_bow]

In [479]:
for document_number, score in sorted(enumerate(sims), key=lambda x: x[1], reverse=True)[:10]:
    print(document_number, score)

17836 0.17677669
27868 0.17149858
5113 0.10976426
28035 0.06299408
18005 0.05812382
0 0.0
1 0.0
2 0.0
3 0.0
4 0.0


In [480]:
# sort the scores in descending order and get the top 10 scores
top_scores = sorted(enumerate(sims), key=lambda x: x[1], reverse=True)[:10]

In [481]:
# create a list of the top 10 paragraphs
top_paragraphs = [combined_paragraphs[idx] for idx, score in top_scores]

# create a list of the corresponding books for the top 10 paragraphs
top_books = [paragraph_book_index[idx] for idx, score in top_scores]

# combine the top paragraphs and their corresponding books into a single string
output = ""
for i in range(len(top_paragraphs)):
    output += f"Book {top_books[i]} - Paragraph {i+1}: {top_paragraphs[i]}\n"

# write the output to a file named "top_paragraphs.txt"
with open("chair.txt", "w") as f:
    f.write(output)

# print the output to the console
print(output)

Book OLturkishempire00goodrich.txt - Paragraph 1: "  5.  The  grand  scheme  of  divine  Providence  which  has  been unfolding  to  the  admiring  view  of  those  who  are  looking  for redemption,  and  God's  providential  dealings  with  myself,  have all  conspired  in  directing  my  attention  to  the  East.  Add  to  all this,  if  you  please,  xe2x80x94 
Book OLfortyyearsintur00goodgoog.txt - Paragraph 2: "  5.  The  grand  scheme  of  divine  Fro  vide  nee  which  lias  been unfolding  to  the  admiring  view  of  those  wbo  are  looking  for redemption,  and  Hod's  providential  dealings  with  myself,  iiave all  conspired  in  directing  my  attention  to  the  Fust,  Add  to  all this,  if  you  please, xe2x80x94 
Book OLconstantinople02grosiala.txt - Paragraph 3: terranean throne; each grasps the Gospel with the dead left liand, and the stiff fingers of the right are arranged as if giving the benediction. Tims always, with the Gospel clutched by their mouldering fin